In [1]:
import pickle
import pandas as pd
import numpy as np
import csv
from sklearn.metrics.pairwise import cosine_similarity
import string
import re

In [2]:
# load glove 
words = pd.read_csv('src/stylesearch/pickles/glove.6B/glove.6B.300d.txt', sep=" ", index_col=0, header=None, quoting=csv.QUOTE_NONE)

In [3]:
def vec(w):
  print(w)
  flat_vec = words.loc[w].values
  return flat_vec.reshape(1, 300)

In [4]:
infile = open('src/stylesearch/pickles/img_to_text.p','rb')
img2text_dict = pickle.load(infile)
infile.close()

In [5]:
def sentence2vec(words_array):
    running_sum = np.zeros((1, 300))
    for word in words_array:
        try: 
            running_sum += vec(word)
        except Exception as e:
            print("This word does not exist in Glove.6B.300:{}.".format(word))
            continue
    return (running_sum/len(words))

In [6]:
text2img_dict = dict()

def text2img_mapping(img2text_dict):
    for img_filename, desc_string  in img2text_dict.items():
        words_array = desc_string.split(" ")
        print(words_array)
        print("current image file being processed", img_filename)
        sentence_vec = sentence2vec(words_array)
        text2img_dict[str(sentence_vec)]= img_filename
    return text2img_dict   

img2vec_dict = dict()

def img2vec_mapping(img2text_dict):
    for img_filename, desc_string  in img2text_dict.items():
        words_array = desc_string.split(" ")
        print(words_array)
        print("current image file being processed", img_filename)
        sentence_vec = sentence2vec(words_array)
        img2vec_dict[img_filename]= sentence_vec
    return img2vec_dict 
        

In [7]:
text2img_dict = text2img_mapping(img2text_dict)
img2vec_dict = img2vec_mapping(img2text_dict)

['your', 'child', 'can', 'use', 'different', 'purposes', 'easel', 'whiteboard', 'one', 'side', 'blackboard', 'other', '']
current image file being processed images/500.210.76.jpg
your
This word does not exist in Glove.6B.300:your.
child
This word does not exist in Glove.6B.300:child.
can
This word does not exist in Glove.6B.300:can.
use
This word does not exist in Glove.6B.300:use.
different
This word does not exist in Glove.6B.300:different.
purposes
This word does not exist in Glove.6B.300:purposes.
easel
This word does not exist in Glove.6B.300:easel.
whiteboard
This word does not exist in Glove.6B.300:whiteboard.
one
This word does not exist in Glove.6B.300:one.
side
This word does not exist in Glove.6B.300:side.
blackboard
This word does not exist in Glove.6B.300:blackboard.
other
This word does not exist in Glove.6B.300:other.

This word does not exist in Glove.6B.300:.
['turned', 'upside', 'down', 'bed', 'quickly', 'converts', 'from', 'low', 'high', 'bed', '']
current image file

with open('text2img_dict', 'wb') as fp:
    pickle.dump(text2img_dict, fp)

with open('img2vec_dict', 'wb') as fp:
    pickle.dump(img2vec_dict, fp)

In [8]:
{'images/500.210.76.jpg': img2text_dict['images/500.210.76.jpg']}

{'images/500.210.76.jpg': 'your child can use different purposes easel whiteboard one side blackboard other '}

In [9]:
# save text2img_dict to pickle

In [10]:
def find_max_similarity(text):
    regex = " *[%s]+ *" % string.punctuation.replace("\\", "\\\\").replace("]", "\\]")
    stop_list = set('for a of the and to in view more product infromation \
                    an w very by has ikea get with as information you it on thats have \
                    price reflects selected options guarantee  brochure year read about terms'.split())
    text = text.lower().split(" ")
    text = [word for word in text if word not in stop_list]
    text = ' '.join(text)
    text = re.sub(regex, " ", text)
    input_vec = sentence2vec(text.split(" "))
    max_similarity = 0
    key_for_max_similarity = None
    for key, value in img2vec_dict.items():
        if max_similarity >= cosine_similarity(img2vec_dict[key], input_vec):
            continue
        else:
            max_similarity = cosine_similarity(img2vec_dict[key], input_vec)
            key_for_max_similarity = key
    return max_similarity, key_for_max_similarity

In [11]:
find_max_similarity("cold play")

cold
This word does not exist in Glove.6B.300:cold.
play
This word does not exist in Glove.6B.300:play.


(0, None)